# Accessibility to green spaces

In [1]:
# If using colab
# Takes around 2-3 min
# !pip install "UrbanAccessAnalyzer[osm,plot,h3] @ git+https://github.com/CityScope/UrbanAccessAnalyzer.git"
# !pip install matplotlib mapclassify folium
# !apt-get install -y osmium-tool


# Restart notebook after installing this if needed

In [2]:
import os
from datetime import datetime, date, timedelta, time
import pandas as pd
import geopandas as gpd
import os

import osmnx as ox

import UrbanAccessAnalyzer.isochrones as isochrones
import UrbanAccessAnalyzer.graph_processing as graph_processing
import UrbanAccessAnalyzer.osm as osm
import UrbanAccessAnalyzer.utils as utils
import UrbanAccessAnalyzer.h3_utils as h3_utils
import UrbanAccessAnalyzer.population as population
import UrbanAccessAnalyzer.poi_utils as poi_utils
import UrbanAccessAnalyzer.plot_helpers as plot_helpers

import zipfile
import numpy as np

## 1 Inputs

In [3]:
city_name = "Parla, España"

In [4]:
download_buffer = 1000 # Download area should be larger than the aoi by 'download_buffer' meters
# It should be max(distance_steps) but there is the risk of downloading an area that is too large

area_steps = [500_000,100_000,50_000, 10_000, 5_000, 1_000] # Grade the green spaces by area in m2 (best to worst)
distance_steps = [250,500,750,1000] # Distance steps for the isochrones (points in the street network reachable in x distance from any point of interest)

min_edge_length = 30 # Simplify street graph to avoid edges of less than 'min_edge_length'

h3_resolution = 10 # If you want results in h3 this is the output h3 resolution

### Results folder

In [5]:
results_path = os.path.normpath("output")

In [6]:
city_filename = utils.sanitize_filename(city_name)
city_results_path = os.path.join(results_path,city_filename)
os.makedirs(results_path,exist_ok=True)
os.makedirs(city_results_path,exist_ok=True)

In [7]:
poi_path = os.path.normpath(city_results_path+"/green_spaces.gpkg")
osm_xml_file = os.path.normpath(city_results_path+"/streets.osm")
streets_graph_path = os.path.normpath(city_results_path+"/streets.graphml")
streets_path = os.path.normpath(city_results_path+"/streets.gpkg")
accessibility_streets_path = os.path.normpath(city_results_path+"/accessibility_streets.gpkg")
population_results_path = os.path.normpath(city_results_path+"/population.gpkg")

### Area of interest
**Area of interest (aoi)**: Polygon. Geographic area where you want to run your analysis.

**Option 1:** From the internet with the city name

In [8]:
aoi = utils.get_city_geometry(city_name)
geo_suggestions = utils.get_geographic_suggestions_from_string(city_name,user_agent="app")
geo_suggestions

{'country_codes': ['ES'],
 'subdivision_names': ['Community of Madrid'],
 'municipalities': ['Parla']}

**Option 2:** Load your own file

In [9]:
# Geographic file (.gpkg, .geojson or .shp)

# aoi = gpd.read_file("")

In [10]:
# csv file with lat/lon columns in geographic coordinates


# df = pd.read_csv("")


# # Create geometry from lon/lat columns
# geometry = gpd.points_from_xy(df["lon"], df["lat"]) # Change column names if needed
# # Convert to GeoDataFrame
# aoi = gpd.GeoDataFrame(
#     df,
#     geometry=geometry,
#     crs="EPSG:4326"  # geographic crs Change if needed
# )

# # OR Parse WKT geometry column
# df["geometry"] = df["geometry"].apply(wkt.loads) # change to match your geometry column name
# # Convert to GeoDataFrame
# aoi = gpd.GeoDataFrame(
#     df,
#     geometry="geometry",
#     crs="EPSG:4326"  # set to whatever CRS the WKT represents
# )

Use UTM coords and create aoi_download with a buffer of X meters. To avoid boundary effects streets and pois should be downloaded for a larger area.

In [11]:
aoi = gpd.GeoDataFrame(geometry=[aoi.union_all()],crs=aoi.crs) # Ensure there is only one polygon
aoi = aoi.to_crs(aoi.estimate_utm_crs()) # Convert to utm

aoi_download = aoi.buffer(download_buffer) # Area to do streets and poi requests 

### Green areas

Polygons of interest (poi)

**Option 1:** Openstreetmap data with an overpass api query

In [12]:
poi = osm.green_areas(bounds=aoi_download)
poi = poi.to_crs(aoi.crs)
poi.to_file(poi_path)
poi

geometry
0   POLYGON ((437758.748 4454593.314, 437751.332 4...
1   POLYGON ((436319.702 4453486.314, 436314.549 4...
2   POLYGON ((435263.258 4456736.673, 435266.862 4...
3   POLYGON ((436165.1 4453481.249, 436170.307 445...
4   POLYGON ((436110.262 4454371.365, 436110.235 4...
..                                                ...
90  POLYGON ((431271.066 4450002.113, 431267.596 4...
91  POLYGON ((431221.181 4449362.515, 431226.365 4...
92  POLYGON ((431035.033 4450062.552, 431030.223 4...
93  POLYGON ((430844.517 4450258.212, 430845.275 4...
94  POLYGON ((430903.467 4450149.647, 430904.039 4...

[95 rows x 1 columns]

In [13]:
# Geographic file (.gpkg, .geojson or .shp)

# poi = gpd.read_file("")

In [14]:
# csv file with lat/lon columns in geographic coordinates


# city_name = "your city name"
# df = pd.read_csv("")

# # Parse WKT geometry column
# df["geometry"] = df["geometry"].apply(wkt.loads) # change to match your geometry column name
# # Convert to GeoDataFrame
# poi = gpd.GeoDataFrame(
#     df,
#     geometry="geometry",
#     crs="EPSG:4326"  # set to whatever CRS the WKT represents
# )

Map of your aoi, the download area (aoi_buffer) and the green areas

In [15]:
m = aoi_download.explore(
    color="red",
    fill=False,
    style_kwds={"weight": 4, "dashArray": "5,5", "opacity": 1.0},
)

m = plot_helpers.general_map(
    m=m,
    aoi=aoi,
    pois=poi,
    color='green',
)
m

## 2 Street graph

### 2.1 Regionwise file and cropping

- Download best regionwise pbf file. (Covers a large area)

- Crop it to cover our area of interest and save it in .osm format

In [16]:
# Select what type of street network you want to load
network_filter = osm.osmium_network_filter("walk+bike+primary")
# Download the region pbf file crop it by aoi and convert to osm format
osm.geofabrik_to_osm(
    osm_xml_file,
    input_file=results_path,
    aoi=aoi_download,
    osmium_filter_args=network_filter,
    overwrite=False
)

File 'output/parla__espana/streets.osm' already exists. Skipping conversion.


'output/parla__espana/streets.osm'

### 2.2 Load to osmnx

This way the street network is a networkx graph

In [17]:
# Load
G = ox.graph_from_xml(osm_xml_file)
# Project geometry coordinates to UTM system to allow euclidean meassurements in meters (sorry americans)
G = ox.project_graph(G,to_crs=aoi.estimate_utm_crs())
# Save the graph in graphml format to avoid the slow loading process
ox.save_graphml(G,streets_graph_path)

### 2.3 Simplify graph

Edges with length smaler than X meters are deleted and its nodes merged

In [18]:
G = graph_processing.simplify_graph(G,min_edge_length=min_edge_length,min_edge_separation=min_edge_length*2,undirected=True)
# Save the result in graphml format
ox.save_graphml(G,streets_graph_path)

street_edges = ox.graph_to_gdfs(G,nodes=False)
street_edges = street_edges.to_crs(aoi.crs)
street_edges.to_file(streets_path)

## 3 Points of interest

### 3.1 Filter by streets

Delete the green spaces that do not contain any street or pedestrian path, as they are not accessible

In [19]:
poi = poi[poi.intersects(street_edges.to_crs(poi.crs).union_all())]

### 3.2 Give each poi a quality grade

Grade depending on the attribute in one column

In [20]:
poi['service_quality'] = poi_utils.quality_by_area(poi,area_steps=area_steps, large_is_better=True)
poi=poi.dropna(subset='service_quality')
poi

/home/miguel/Documents/Proyectos/PTLevelofService/accessibility/UrbanAccessAnalyzer/.venv/lib/python3.12/site-packages/geopandas/geodataframe.py:1968: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)


geometry  service_quality
0   POLYGON ((437758.748 4454593.314, 437751.332 4...            0.333
2   POLYGON ((435263.258 4456736.673, 435266.862 4...            1.000
6   POLYGON ((435428.423 4454185.918, 435432.287 4...            0.500
7   POLYGON ((435208.858 4453405.18, 435208.642 44...            0.833
10  POLYGON ((435437.105 4454470.208, 435437.062 4...            0.167
13  POLYGON ((434597.259 4453046.77, 434595.774 44...            0.833
14  POLYGON ((435303.111 4455200.474, 435363.071 4...            0.333
16  POLYGON ((435027.334 4454018.292, 435019.713 4...            0.333
18  POLYGON ((435045.113 4453538.533, 435052.445 4...            0.333
24  POLYGON ((434848.762 4454867.819, 434841.415 4...            0.167
25  POLYGON ((434558.534 4454747.884, 434550.471 4...            0.500
28  POLYGON ((434624.906 4453964.273, 434616.364 4...            0.167
29  POLYGON ((434527.696 4453667.57, 434528.705 44...            0.500
30  POLYGON ((433989.554 4455682.272, 433985.491 4...            0.500
33  POLYGON ((434428.791 4454375.893, 434422.908 4...            0.167
34  POLYGON ((434361.746 4453597.312, 434353.972 4...            0.333
35  POLYGON ((434292.59 4454151.736, 434292.603 44...            0.333
36  POLYGON ((433896.464 4453472.498, 433891.596 4...            0.500
37  POLYGON ((434300.348 4454773.775, 434293.266 4...            0.167
38  POLYGON ((434242.861 4455078.918, 434235.639 4...            0.333
39  POLYGON ((434099.741 4453804.377, 434092.783 4...            0.333
41  POLYGON ((434152.402 4455316.035, 434143.226 4...            0.167
42  POLYGON ((434120.947 4452906.763, 434121.837 4...            0.333
43  POLYGON ((434095.504 4454761.733, 434090.475 4...            0.167
44  POLYGON ((433982.304 4455430.659, 433986.83 44...            0.500
46  POLYGON ((433996.161 4454314.292, 433992.524 4...            0.167
48  POLYGON ((433779.444 4454065.297, 433781.926 4...            0.500
49  POLYGON ((433844.139 4455355.038, 433838.554 4...            0.333
51  POLYGON ((433812.855 4453955.476, 433817.099 4...            0.167
52  POLYGON ((433432.995 4453506.602, 433433.562 4...            0.833
53  POLYGON ((433713.706 4454282.041, 433709.299 4...            0.333
54  POLYGON ((433682.627 4454187.083, 433690.555 4...            0.333
83  POLYGON ((431162.757 4456095.874, 431163.041 4...            0.667
84  POLYGON ((431279.915 4455492.24, 431281.649 44...            0.167

### 3.3 Convert polygons of interest to points of interest

This is done by taking from the boundary of the polygon the intersecting points with streets. 

Requires every green space to contain some pedestrian paths to be considered valid and dicards non visitable spaces. 

In [21]:
poi_points = poi_utils.polygons_to_points(poi,street_edges)
poi_points

service_quality  poi_id                        geometry
0              0.333       0   POINT (437757.976 4454593.51)
1              1.000       2  POINT (435361.385 4456362.719)
2              1.000       2  POINT (436024.396 4456498.643)
3              1.000       2  POINT (435236.667 4456416.043)
4              1.000       2  POINT (435255.661 4456847.271)
..               ...     ...                             ...
266            0.667      83  POINT (431315.526 4455900.611)
267            0.667      83  POINT (431282.462 4455498.036)
268            0.667      83  POINT (431159.371 4456070.761)
269            0.167      84  POINT (431228.625 4455306.367)
270            0.167      84  POINT (431281.437 4455489.956)

[271 rows x 3 columns]

Lets see everything on a map

In [22]:
m = plot_helpers.general_map(
    aoi=aoi,
    pois=[poi_points,poi],
    cmap='Greens',
    column='service_quality'
)
m

### 3.4 Add Points of interest to graph

In [23]:
G, osmids = graph_processing.add_points_to_graph(
    poi_points,
    G,
    max_dist=100+min_edge_length, # Maximum distance from point to graph edge to project the point
    min_edge_length=min_edge_length # Minimum edge length after adding the new nodes
)
poi_points['osmid'] = osmids # Add the ids of the nodes in the graph to points

## 4 Compute isochrones

### 4.1 Distance matrix 

Create matrix relating distance and service quality to an access grade (0-1)

In [24]:
distance_matrix, accessibility_grades = isochrones.default_distance_matrix(
    poi_points,
    distance_steps,
    service_quality_column="service_quality"
)
distance_matrix

250    500    750   1000  service_quality
0  1.000  0.889  0.778  0.667            1.000
1  0.889  0.778  0.667  0.556            0.833
2  0.778  0.667  0.556  0.444            0.667
3  0.667  0.556  0.444  0.333            0.500
4  0.556  0.444  0.333  0.222            0.333
5  0.444  0.333  0.222  0.111            0.167

### 4.2 Isochrones

In [25]:
accessibility_graph = isochrones.graph(
    G,
    poi_points,
    distance_matrix=distance_matrix, # If service_quality_col is None it could be a list of distances
    service_quality_col = 'service_quality', # If all points have the same quality this could be None
    accessibility_values = accessibility_grades, # could be None and it will set to the sorted unique values of the matrix
    min_edge_length = min_edge_length # Do not add new nodes if there will be an edge with less than this length
)
# Save edges as gpkg
accessibility_nodes, accessibility_edges = ox.graph_to_gdfs(accessibility_graph)
crs = accessibility_nodes.crs
for s in np.unique(distance_matrix['service_quality']):
    ls = distance_matrix.loc[distance_matrix['service_quality'] == s,distance_matrix.columns[0]].iloc[0]
    poi_s = poi[poi['service_quality'] == s]
    if len(poi_s) == 0:
        continue 

    accessibility_nodes.loc[accessibility_nodes.intersects(poi_s.to_crs(crs).union_all()),'accessibility'] = ls
    accessibility_edges.loc[accessibility_edges.intersects(poi_s.to_crs(crs).union_all()),'accessibility'] = ls

accessibility_graph = ox.graph_from_gdfs(accessibility_nodes,accessibility_edges)
accessibility_edges.to_file(accessibility_streets_path)

100%|██████████| 24/24 [00:02<00:00, 10.33it/s]


#### Lets visualize the results on a map

### 4.3 Convert to H3

In [26]:
access_h3_df = h3_utils.from_gdf(
    accessibility_edges,
    resolution=h3_resolution,
    columns=['accessibility'],
    contain="overlap",
    method="max",
    buffer=10
)

access_h3_df

accessibility
h3_cell                      
8a390c168b4ffff         0.444
8a390c16900ffff         0.444
8a390c169017fff         0.556
8a390c16901ffff         0.444
8a390c169047fff         0.111
...                       ...
8a390cb9b71ffff         0.667
8a390cb9b74ffff         0.778
8a390cb9b757fff         0.778
8a390cb9b75ffff         0.778
8a390cb9b78ffff         0.778

[1083 rows x 1 columns]

See everything on a map

In [27]:
m = plot_helpers.general_map(
    aoi=aoi,
    pois=[poi,poi_points],
    gdfs=[access_h3_df,accessibility_edges],
    cmap="RdYlGn",
    column="accessibility",
    poi_cmap="Greens",
    poi_column="service_quality"
)
m.save(city_results_path+"/access_map.html")
m

## 5 Population

### 5.1 Download Worldpop tif file

- One file for every country
- 100m pixel size
- tif format
- available from 2000 to 2030
- gender and age

In [28]:
population_file = population.download_worldpop_population(
    aoi_download,
    2025,
    folder=results_path,
    resolution="100m",
)

Raster population path output/esp_pop_2025_CN_100m_R2025A_v1.tif exists. Skipping download...


In [29]:
pop_h3_df = h3_utils.from_raster(population_file,aoi=aoi_download,resolution=h3_resolution)
pop_h3_df = pop_h3_df.rename(columns={'value':'population'})

### 5.2 Assign level of service to each population cell

In [30]:
results_h3_df = access_h3_df.merge(pop_h3_df,left_index=True,right_index=True,how='outer')
results_h3_df = h3_utils.to_gdf(results_h3_df).to_crs(aoi.crs)
results_h3_df = results_h3_df[results_h3_df.intersects(aoi.union_all())]
results_h3_df.to_file(population_results_path)
results_h3_df

accessibility  population  \
h3_cell                                     
8a390c14da67fff           NaN    0.017219   
8a390c14da6ffff           NaN    0.022777   
8a390c14db27fff           NaN   15.810202   
8a390c14db2ffff           NaN    5.984092   
8a390c14db47fff           NaN    0.565470   
...                       ...         ...   
8a390cab6d87fff           NaN    0.000029   
8a390cab6d8ffff           NaN    7.459510   
8a390cab6d9ffff           NaN    0.488091   
8a390cab6da7fff           NaN    0.000058   
8a390cab6daffff           NaN    3.428287   

                                                          geometry  
h3_cell                                                             
8a390c14da67fff  POLYGON ((433417.373 4451903.505, 433347.273 4...  
8a390c14da6ffff  POLYGON ((433546.964 4451881.633, 433476.865 4...  
8a390c14db27fff  POLYGON ((432850.103 4452118.963, 432779.999 4...  
8a390c14db2ffff  POLYGON ((432979.701 4452097.089, 432909.598 4...  
8a390c14db47fff  POLYGON ((433238.893 4452053.343, 433168.792 4...  
...                                                            ...  
8a390cab6d87fff  POLYGON ((432102.007 4453442.435, 432031.898 4...  
8a390cab6d8ffff  POLYGON ((432231.613 4453420.552, 432161.506 4...  
8a390cab6d9ffff  POLYGON ((432150.896 4453314.461, 432080.788 4...  
8a390cab6da7fff  POLYGON ((432053.117 4453570.409, 431983.008 4...  
8a390cab6daffff  POLYGON ((432182.724 4453548.525, 432112.616 4...  

[1437 rows x 3 columns]

In [31]:
pop_gdf_points = results_h3_df.copy()
pop_gdf_points.geometry = pop_gdf_points.geometry.centroid
pop_gdf_points = pop_gdf_points.dropna(subset=['population'])
pop_gdf_points = pop_gdf_points[pop_gdf_points['population'] > 1]
m = plot_helpers.general_map(
    aoi=aoi,
    pois=[poi,poi_points],
    gdfs=[pop_gdf_points],
    cmap="RdYlGn",
    column="accessibility",
    size_column="population",
    poi_column="service_quality",
    poi_cmap="Greens",
)
m.save(city_results_path+"/population_map.html")
m

## Statistics

In [34]:
stats_df = results_h3_df.groupby('accessibility', as_index=False)['population'].sum()
stats_df = stats_df.sort_values("accessibility",ascending=False)
total_population = stats_df['population'].sum()
stats_df = pd.concat([stats_df, pd.DataFrame([{'accessibility': 'total population', 'population': total_population}])], ignore_index=True)
stats_df['population %'] = (stats_df['population'] * 100 / total_population).round(2)
stats_df['population'] = stats_df['population'].round(0).astype(int)
stats_df.to_csv(city_results_path + "/stats.csv")
stats_df

accessibility  population  population %
0               1.0         105          0.08
1             0.889       26190         19.93
2             0.778       28228         21.48
3             0.667       42298         32.19
4             0.556       26217         19.95
5             0.444        6273          4.77
6             0.333        1567          1.19
7             0.222         511          0.39
8             0.111           0          0.00
9  total population      131389        100.00

In [33]:
# !zip -r /content/output.zip "{results_path}" # For colab. Export the output folder as zip.

Important files:

- streets.gpkg Has the street geometry as lines (all streets)
- accessibility.gpkg Has the street geometry as lines with the accessibility score (only streets with score > 0)
- population.gpkg Is a grid with population and level of service
- stats.csv Population statistics